In [2]:
import os
os.environ['DATA_ROOT'] = '/work/sarandi/data'
import smplfit.tf

#fitter_tf = smplfit.tf.get_cached_fit_fn()


In [3]:
%cd ..

/home/sarandi/rwth-home2/pose/pycharm/smplfit


/home/sarandi/micromamba/envs/py10/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [1]:
import smplfit.pt
import os
os.environ['DATA_ROOT'] = '/work/sarandi/data'

In [3]:
import torch

pose_rotvecs = torch.rand((1, 72)).cuda()  # Random values in range [0, 1)
shape_betas = torch.zeros((1, 10)).cuda()
#res = bm(pose_rotvecs=pose_rotvecs, shape_betas=shape_betas)

@torch.jit.script
def bm_forward(pose_rotvecs, shape_betas, trans, kid_factor, rel_rotmats, glob_rotmats, return_vertices):
    bm = smplfit.pt.SMPL()
    return bm(pose_rotvecs, shape_betas, trans, kid_factor, rel_rotmats, glob_rotmats, return_vertices)
# apply torch jit to the forward pass

                
trans = torch.zeros((1, 3)).cuda()
kid_factor = torch.zeros((1,)).cuda()
rel_rotmats = None
glob_rotmats = None
return_vertices = torch.tensor(True).cuda()

res = bm_forward(pose_rotvecs, shape_betas, trans, kid_factor, rel_rotmats, glob_rotmats, return_vertices)
v = res['vertices']
j = res['joints']

FrontendError: Cannot instantiate class 'SMPL' in a script function:
  File "/tmp/ipykernel_2318563/1728192146.py", line 9
@torch.jit.script
def bm_forward(pose_rotvecs, shape_betas, trans, kid_factor, rel_rotmats, glob_rotmats, return_vertices):
    bm = smplfit.pt.SMPL()
         ~~~~~~~~~~~~~~~~~~~~ <--- HERE
    return bm(pose_rotvecs, shape_betas, trans, kid_factor, rel_rotmats, glob_rotmats, return_vertices)


In [6]:
import smplfit.pt.fitting

# repeat v and j 100 times
v_ = v.repeat(100, 1, 1).cuda()
j_ = j.repeat(100, 1, 1).cuda()

f = smplfit.pt.fitting.SMPLfit(bm.cuda(), num_betas=10)

fitres = f.fit(target_vertices=v_, target_joints=j_, n_iter=3, beta_regularizer=0, beta_regularizer2=0,
               final_adjust_rots=True, requested_keys=['pose_rotvecs', 'shape_betas'])

In [15]:
v_ = v_.cuda()
j_ = j_.cuda()

In [17]:
f.body_model = f.body_model.cuda()

In [9]:
%%timeit

fitres = f.fit(target_vertices=v_, target_joints=j_, n_iter=3, beta_regularizer=1, beta_regularizer2=0,
               final_adjust_rots=True, requested_keys=['pose_rotvecs', 'shape_betas'])

100 ms ± 2.02 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [11]:
fit_forw = bm(pose_rotvecs=fitres['pose_rotvecs'], shape_betas=fitres['shape_betas'])

In [13]:
torch.linalg.norm(fit_forw['vertices'] - v_, dim=-1).mean()

tensor(0.0028, device='cuda:0')

In [7]:
glob_rots = f.fit_global_rotations(v, f.default_mesh_tf[None], j, f.body_model.J_template[None],
                                   vertex_weights=None, joint_weights=None)

In [1]:
from smplfit.tf.rotation import kabsch as kabsch_tf
from smplfit.pt.rotation import kabsch

import numpy as np
import torch


# set up two random point clouds
X = np.random.rand(100, 3)
Y = np.random.rand(100, 3)

# compute the rotation matrix
R = kabsch(torch.tensor(X), torch.tensor(Y))
R_tf = kabsch_tf(X, Y)

2024-10-15 22:08:27.067981: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-10-15 22:08:27.068014: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-10-15 22:08:27.069221: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-10-15 22:08:27.075440: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-10-15 22:08:27.722687: W tensorflow/compiler/tf2

In [2]:
R, R_tf

(tensor([[ 0.3657, -0.2495,  0.8967],
         [ 0.8759,  0.4181, -0.2408],
         [-0.3148,  0.8735,  0.3714]], dtype=torch.float64),
 <tf.Tensor: shape=(3, 3), dtype=float64, numpy=
 array([[ 0.3656626 , -0.24953579,  0.89667316],
        [ 0.87589646,  0.41809366, -0.24083831],
        [-0.31479558,  0.8734584 ,  0.37144873]])>)

In [14]:
import smplfit.tf
import tensorflow as tf
bm_tf = smplfit.tf.get_cached_body_model()

pose_rotvecs_tf = tf.random.uniform((1, 72))
res_tf = bm_tf(pose_rotvecs=tf.convert_to_tensor(pose_rotvecs_tf.numpy()), shape_betas=tf.zeros((1, 10)))
v_tf = res_tf['vertices']
j_tf = res_tf['joints']

import smplfit.tf.fitting

fitter_tf = smplfit.tf.fitting.SMPLfit(bm_tf, num_betas=10)
#fitres_tf = fitter_tf.fit(to_fit=v, joints_to_fit=j, n_iter=3, l2_regularizer=0, l2_regularizer2=0, final_adjust_rots=True)

fit_fn = smplfit.tf.get_cached_fit_fn(num_iter=3, l2_regularizer=0, l2_regularizer2=0, final_adjust_rots=True)


In [17]:
%%timeit
fitres_tf = fit_fn(v_tf, j_tf)


34.4 ms ± 2.72 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [9]:
f_tf = fitter_tf
glob_rots_tf = f_tf.fit_global_rotations(v_tf, f_tf.default_mesh_tf[None], j_tf,
                                         f_tf.body_model.J_template[None], vertex_weights=None,
                                         joint_weights=None)
glob_rots_tf

<tf.Tensor: shape=(1, 24, 3, 3), dtype=float32, numpy=
array([[[[ 7.73086369e-01, -2.34770581e-01,  5.89253902e-01],
         [ 5.34347534e-01,  7.41604567e-01, -4.05580282e-01],
         [-3.41775090e-01,  6.28414869e-01,  6.98773503e-01]],

        [[ 5.23969531e-03,  3.89897913e-01,  9.20843124e-01],
         [ 9.97355103e-01, -6.87939748e-02,  2.34531760e-02],
         [ 7.24928081e-02,  9.18284833e-01, -3.89227033e-01]],

        [[-1.33563876e-02,  2.83898294e-01,  9.58761215e-01],
         [ 9.91213977e-01, -1.22428641e-01,  5.00607193e-02],
         [ 1.31592050e-01,  9.51006055e-01, -2.79769003e-01]],

        [[ 7.86862373e-02,  4.61987704e-01,  8.83388996e-01],
         [ 8.43663812e-01,  4.41207826e-01, -3.05887043e-01],
         [-5.31074107e-01,  7.69352496e-01, -3.55045259e-01]],

        [[-7.49345794e-02,  5.37845075e-01,  8.39706838e-01],
         [ 4.21443880e-01, -7.46091723e-01,  5.15492260e-01],
         [ 9.03753221e-01,  3.92517626e-01, -1.70763344e-01]],

     

In [4]:
from pygltflib import GLTF2
glb_file = GLTF2().load("/home/sarandi/Downloads/xdata_blueman.glb")

In [5]:
glb_file

GLTF2(extensions={'FB_momentum': {'fps': 240.0, 'motion': {'jointNames': ['body_world', 'b_root', 'b_spine0', 'b_spine1', 'b_spine2', 'b_spine3', 'b_neck0', 'b_head', 'b_head_null', 'b_l_eye', 'b_l_eye_null', 'b_r_eye', 'b_r_eye_null', 'b_jaw', 'b_jaw_null', 'b_teeth', 'b_tongue0', 'b_tongue1', 'b_tongue2', 'b_tongue3', 'b_tongue4', 'b_l_tongue4_1', 'b_l_tongue4_2', 'b_r_tongue4_1', 'b_r_tongue4_2', 'b_l_tongue3_1', 'b_l_tongue3_2', 'b_r_tongue3_1', 'b_r_tongue3_2', 'b_l_tongue2_1', 'b_l_tongue2_2', 'b_r_tongue2_1', 'b_r_tongue2_2', 'b_r_tongue1_1', 'b_r_tongue1_2', 'b_l_tongue1_1', 'b_l_tongue1_2', 'p_neck_twist0', 'p_neck_twist1', 'b_r_shoulder', 'p_r_delt', 'p_r_scap', 'b_r_arm', 'p_r_arm_twist4', 'p_r_arm_twist3', 'p_r_arm_twist2', 'p_r_arm_twist1', 'p_r_arm_twist0', 'b_r_forearm', 'p_r_forearm_twist0', 'p_r_forearm_twist1', 'p_r_forearm_twist2', 'p_r_forearm_twist3', 'p_r_forearm_twist4', 'b_r_wrist_twist', 'b_r_wrist', 'b_r_index1', 'b_r_index2', 'b_r_index3', 'b_r_index_null', '

In [6]:
meshes = glb_file.meshes
for mesh in meshes:
    print(mesh)

Mesh(extensions={}, extras={}, primitives=[Primitive(extensions={}, extras={}, attributes=Attributes(POSITION=1, NORMAL=None, TANGENT=None, TEXCOORD_0=None, TEXCOORD_1=None, COLOR_0=2, JOINTS_0=None, WEIGHTS_0=None), indices=0, mode=4, material=None, targets=[])], weights=[], name=None)
Mesh(extensions={}, extras={}, primitives=[Primitive(extensions={}, extras={}, attributes=Attributes(POSITION=4, NORMAL=None, TANGENT=None, TEXCOORD_0=None, TEXCOORD_1=None, COLOR_0=5, JOINTS_0=None, WEIGHTS_0=None), indices=3, mode=4, material=None, targets=[])], weights=[], name=None)
Mesh(extensions={}, extras={}, primitives=[Primitive(extensions={}, extras={}, attributes=Attributes(POSITION=7, NORMAL=None, TANGENT=None, TEXCOORD_0=None, TEXCOORD_1=None, COLOR_0=8, JOINTS_0=None, WEIGHTS_0=None), indices=6, mode=4, material=None, targets=[])], weights=[], name=None)
Mesh(extensions={}, extras={}, primitives=[Primitive(extensions={}, extras={}, attributes=Attributes(POSITION=10, NORMAL=None, TANGENT=N

In [8]:
import numpy as np
# Get mesh information (assuming the first mesh and primitive)
first_mesh = glb_file.meshes[0]
first_primitive = first_mesh.primitives[0]

# Get the position accessor index
position_accessor_index = first_primitive.attributes.POSITION

# Get the accessor and buffer view for the positions
position_accessor = glb_file.accessors[position_accessor_index]
position_buffer_view = glb_file.bufferViews[position_accessor.bufferView]

# Get the raw buffer data
buffer = glb_file.buffers[position_buffer_view.buffer]
buffer_data = buffer.uri  # This is the raw binary data for the positions

# Extract the byte offset, stride, and total count of vertices
byte_offset = position_buffer_view.byteOffset + position_accessor.byteOffset
vertex_count = position_accessor.count
component_type = position_accessor.componentType  # Usually FLOAT (5126)
byte_stride = position_buffer_view.byteStride if position_buffer_view.byteStride else 12  # 3 floats per vertex (3 * 4 bytes)

# Convert the buffer data to a NumPy array of floats
vertex_data = np.frombuffer(buffer_data, dtype=np.float32, count=vertex_count*3, offset=byte_offset)

# Reshape into (n_vertices, 3)
vertices = vertex_data.reshape(vertex_count, 3)

# Now `vertices` is a NumPy array of shape (n_vertices, 3)
print(vertices)

TypeError: a bytes-like object is required, not 'NoneType'

In [10]:
buffer

Buffer(extensions={}, extras={}, uri=None, byteLength=775792540)

In [11]:
glb_file.skins

[Skin(extensions={}, extras={}, inverseBindMatrices=241, skeleton=1, joints=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159], name=None)]

In [12]:
vertices = []
for mesh in glb_file.meshes:
    for primitive in mesh.primitives:
        positions = glb_file.accessors[primitive.attributes.POSITION]
        bufferView = glb_file.bufferViews[positions.bufferView]
        buffer = glb_file.buffers[bufferView.buffer]
        vertices.append(buffer[bufferView.byteOffset:bufferView.byteOffset + bufferView.byteLength])


TypeError: 'Buffer' object is not subscriptable

In [16]:
# Function to get data from buffer
def get_buffer_data(buffer, buffer_view):
    # Extract the relevant slice of data from the buffer
    start = buffer_view.byteOffset
    end = start + buffer_view.byteLength
    return buffer[start:end]

# Extract vertex positions
def extract_vertices(glb_file):
    vertices = []
    for mesh in glb_file.meshes:
        for primitive in mesh.primitives:
            position_accessor_idx = primitive.attributes.POSITION
            position_accessor = glb_file.accessors[position_accessor_idx]
            buffer_view_idx = position_accessor.bufferView
            buffer_view = glb_file.bufferViews[buffer_view_idx]
            buffer = glb_file.buffers[buffer_view.buffer]

            # Get the vertex data
            raw_data = get_buffer_data(buffer, buffer_view)
            
            # Convert the raw data into usable floats (assuming float32 for vertex positions)
            vertex_positions = np.frombuffer(raw_data, dtype=np.float32)
            vertices.append(vertex_positions.reshape(-1, 3))  # Reshape to (n_vertices, 3)

    return vertices

# Extract vertices from the loaded GLB file
vertices = extract_vertices(glb_file)

# Print the shape of the first mesh's vertices
print(vertices[0].shape)  # (n_vertices, 3)

{'extensions': {}, 'extras': {}, 'uri': None, 'byteLength': 775792540}


TypeError: 'Buffer' object is not subscriptable

In [17]:
glb_file.buffers

[Buffer(extensions={}, extras={}, uri=None, byteLength=775792540)]

In [19]:
import bpy
import numpy as np

# Load the GLB file
bpy.ops.import_scene.gltf(filepath="/home/sarandi/Downloads/xdata_blueman.glb")

# Get the imported object (assuming the first mesh in the scene is the target)
obj = bpy.context.selected_objects[0]

# Switch to object mode (to avoid edit mode conflicts)
bpy.ops.object.mode_set(mode='OBJECT')

# Get the mesh data
mesh = obj.data

# Function to extract vertices in world coordinates
def get_world_vertices(obj):
    obj.update_from_editmode()  # Ensure mesh is updated
    verts = [obj.matrix_world @ v.co for v in obj.data.vertices]  # Transform local to world space
    return np.array(verts)

# Go through the animation frame by frame
scene = bpy.context.scene
start_frame = scene.frame_start
end_frame = scene.frame_end

for frame in range(start_frame, end_frame + 1):
    scene.frame_set(frame)  # Set the scene to the desired frame
    
    # Get vertex positions for the current frame
    vertices = get_world_vertices(obj)
    
    # Print or process the vertex positions for each frame
    print(f"Frame {frame}: Vertex Positions:\n", vertices)

Data are loaded, start creating Blender stuff
glTF import finished in 116.72s


AttributeError: 'Armature' object has no attribute 'vertices'

In [24]:
scene.frame_set(10) 

In [39]:
dir(obj.data)

['__doc__',
 '__module__',
 '__slots__',
 'animation_data',
 'animation_data_clear',
 'animation_data_create',
 'asset_clear',
 'asset_data',
 'asset_generate_preview',
 'asset_mark',
 'axes_position',
 'bl_rna',
 'bones',
 'copy',
 'display_type',
 'edit_bones',
 'evaluated_get',
 'is_editmode',
 'is_embedded_data',
 'is_evaluated',
 'is_library_indirect',
 'is_runtime_data',
 'layers',
 'layers_protected',
 'library',
 'library_weak_reference',
 'make_local',
 'name',
 'name_full',
 'original',
 'override_create',
 'override_hierarchy_create',
 'override_library',
 'override_template_create',
 'pose_position',
 'preview',
 'preview_ensure',
 'rna_type',
 'show_axes',
 'show_bone_custom_shapes',
 'show_group_colors',
 'show_names',
 'tag',
 'transform',
 'update_tag',
 'use_extra_user',
 'use_fake_user',
 'use_mirror_x',
 'user_clear',
 'user_of_id',
 'user_remap',
 'users']

In [49]:
for obj in bpy.context.scene.objects:
    if obj.type == 'MESH':
        # Select the object
        bpy.context.view_layer.objects.active = obj
        obj.select_set(True)
        
        # Apply the armature modifier (if present)
        bpy.ops.object.convert(target='MESH')
        
        # Deselect the object after conversion
        obj.select_set(False)
        # print name of the object
        print(obj.name)
        print(len(obj.data.vertices))

pBackOfHead
8
pTopOfHead
8
pRightAuricularis
8
pLeftAuricularis
8
pCenterOfHead
8
pC7SpinalProcess
8
pRightTopOfHand
8
pRightPinky
8
pRightHandController
8
pRightUlnarStyloid
8
pRightBallHand
8
pRightRadialStyloid
8
pRightHandPalm
8
pRightOlecranon
8
pRightUlnarPosteriorBorder
8
pRightArmMedEpicondyle
8
pRightArmLatEpicondyle
8
pRightAcromion
8
pLeftTopOfHand
8
pLeftPinky
8
pLeftHandController
8
pLeftHandPalm
8
pLeftUlnarStyloid
8
pLeftBallHand
8
pLeftRadialStyloid
8
pLeftUlnarPosteriorBorder
8
pLeftOlecranon
8
pLeftArmMedEpicondyle
8
pLeftArmLatEpicondyle
8
pLeftAcromion
8
pIJ
8
pPX
8
pT4SpinalProcess
8
pT8SpinalProcess
8
pT12SpinalProcess
8
pL3SpinalProcess
8
pL5SpinalProcess
8
pLeftSIPS
8
pThoracolumbarFascia
8
pSacrum
8
pRightSIPS
8
pRightCSI
8
pRightASI
8
pLeftCSI
8
pLeftASI
8
pRightFifthMetatarsal
8
pRightFirstMetatarsal
8
pRightPivotFoot
8
pRightToe
8
pRightHeelFoot
8
pRightTopOfFoot
8
pRightHeelCenter
8
pRightFibula
8
pRightLatMalleolus
8
pRightMedMalleolus
8
pRightTibialTub
8


In [41]:
def extract_mesh_data(obj):
    mesh = obj.data
    vertices = [obj.matrix_world @ v.co for v in mesh.vertices]
    faces = [[v for v in poly.vertices] for poly in mesh.polygons]
    return vertices, faces

In [50]:
posed_obj = [obj for obj in bpy.context.scene.objects if obj.type == 'MESH' and obj.name=='mesh'][0]
vertices, faces = extract_mesh_data(posed_obj)

In [52]:
import trimesh
trm = trimesh.Trimesh(vertices, faces)

/home/sarandi/micromamba/envs/py10/lib/python3.10/site-packages/numpy/core/getlimits.py:549: UserWarning: The value of the smallest subnormal for <class 'numpy.float64'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/home/sarandi/micromamba/envs/py10/lib/python3.10/site-packages/numpy/core/getlimits.py:89: UserWarning: The value of the smallest subnormal for <class 'numpy.float64'> type is zero.
  return self._float_to_str(self.smallest_subnormal)
/home/sarandi/micromamba/envs/py10/lib/python3.10/site-packages/numpy/core/getlimits.py:549: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/home/sarandi/micromamba/envs/py10/lib/python3.10/site-packages/numpy/core/getlimits.py:89: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  return self._float_to_str(self.smallest_subnormal)


In [54]:
trm.show()

In [15]:
import torch
import os
DATA_ROOT = '/work/sarandi/data'
import simplepyutils as spu
import numpy as np

def scipy2torch_csr(sparse_matrix):
    return torch.sparse_csr_tensor(
        torch.from_numpy(sparse_matrix.indptr),
        torch.from_numpy(sparse_matrix.indices),
        torch.from_numpy(sparse_matrix.data),
        sparse_matrix.shape)

smpl2smplx_mat = (spu.load_pickle(
    f'{DATA_ROOT}/body_models/smpl2smplx_deftrafo_setup.pkl'
)['mtx'].tocsr()[:, :6890]).astype(np.float32)
smplx2smpl_mat = (spu.load_pickle(
    f'{DATA_ROOT}/body_models/smplx2smpl_deftrafo_setup.pkl'
)['mtx'].tocsr()[:, :10475]).astype(np.float32)

smpl2smplx_mat = scipy2torch_csr(smpl2smplx_mat)
smplx2smpl_mat = scipy2torch_csr(smplx2smpl_mat)



In [17]:
smplx_ex = torch.rand((2, 10475, 3))
torch.sparse.mm(smplx2smpl_mat, smplx_ex)

RuntimeError: mat2 must be a matrix, got 3-D tensor

In [12]:
smplx2smpl_mat = (spu.load_pickle(
    f'{DATA_ROOT}/body_models/smplx2smpl_deftrafo_setup.pkl'
)['mtx'].tocsr()[:, :10475]).astype(np.float32)

scipy2torch_csr(smplx2smpl_mat).shape

torch.Size([6890, 10475])

In [20]:
def smplx_verts_to_smpl_verts(smplx_verts):
    v = smplx_verts.permute(1, 0, 2).reshape(10475, -1)
    r = torch.sparse.mm(smplx2smpl_mat, v)
    return r.reshape(6890, -1, 3).permute(1, 0, 2)


In [21]:
out = smplx_verts_to_smpl_verts(smplx_ex)

In [22]:
out.shape

torch.Size([2, 6890, 3])

In [61]:
from smplfit.pt.converter import BodyModelConverter
converter = BodyModelConverter('smplx', 'neutral', 'smpl', 'neutral')


In [69]:
pose = torch.randn((2, 55*3)) * 0.3
shape = torch.zeros((2, 10))
trans = torch.zeros((2, 3))
pose_, shape_, trans_ = converter.convert(pose, shape, trans)

In [70]:
res1 = converter.body_model_in(pose, shape, trans)
res2 = converter.body_model_out(pose_, shape_, trans_)

In [85]:
torch.linalg.norm(converter2.convert_vertices(res2['vertices']) - res1['vertices'], dim=-1).mean()

tensor(0.0108)

In [83]:
res2['vertices'].shape

torch.Size([2, 6890, 3])

In [84]:
converter2 = BodyModelConverter('smpl', 'neutral', 'smplx', 'neutral')

In [86]:
pose.shape, pose_.shape

(torch.Size([2, 165]), torch.Size([2, 72]))

In [88]:
pose_basic = pose_.clone()
pose_basic[:, 3:22*3] = pose[:, 3:22*3]
pose_basic[:, 22*3:] = 0
res_basic = converter.body_model_out(pose_basic, shape, trans) 

In [89]:
import trimesh

m = trimesh.Trimesh(vertices=res_basic['vertices'][0].cpu().numpy(), faces=converter.body_model_out.faces)

In [90]:
m.show()

In [91]:
import trimesh

m2 = trimesh.Trimesh(vertices=res2['vertices'][0].cpu().numpy(), faces=converter.body_model_out.faces)
m2.show()

In [92]:
import trimesh

m3 = trimesh.Trimesh(vertices=res1['vertices'][0].cpu().numpy(), faces=converter.body_model_in.faces)
m3.show()

NameError: name 'vertices' is not defined

In [9]:
from smplfit.np.fitting import Fitter
from smplfit.np.smpl import SMPL
import numpy as np
import os
os.environ['DATA_ROOT'] = '/work/sarandi/data'
vertex_subset = np.arange(0, 6890, 10)  # the indices of the vertices

pose = np.random.randn(1, 24*3) * 0.5
shape = np.zeros((1, 10))
 

#regressor = np.random.randn(24, 689)
#vertices = np.random.randn(1, 689, 3)

body_model = SMPL(model_name='smpl', gender='neutral')
res = body_model(pose_rotvecs=pose, shape_betas=shape)
v = res['vertices']


fitter = Fitter(body_model, num_betas=10)
fit_result = fitter.fit(v, n_iter=3, beta_regularizer=1,
                        requested_keys=['pose_rotvecs', 'shape_betas'])
fit_result['pose_rotvecs'], fit_result['shape_betas'], fit_result['trans']

(array([[ 3.43803138e-01, -2.20808457e-01, -6.92372408e-01,
         -5.06447729e-02, -3.87231580e-01, -6.95032334e-01,
         -7.10928830e-01,  2.52361328e-01,  6.59525383e-01,
         -1.14854590e-01, -1.58066550e-01, -1.02816576e+00,
          3.49107852e-01, -4.29348689e-02,  2.46299114e-01,
          5.06520656e-01,  3.69976811e-02, -3.40311166e-01,
         -9.30977435e-01,  5.10898616e-01, -3.69022804e-01,
          4.32357873e-01, -9.54667280e-01,  5.34487778e-03,
          1.75258113e-01,  1.10408195e+00,  1.23590394e+00,
          8.85052901e-02, -3.99122564e-01,  4.70620648e-01,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         -7.24495609e-01,  2.22920398e-01,  8.23521444e-01,
         -6.78219581e-01, -3.07638056e-01,  1.26491955e+00,
          2.40643986e-01,  1.67383352e-01, -8.49468410e-01,
          6.45015942e-01,  8.51895698e-01,  1.98964278e-01,
          2.63447538e-01,  2.82337760e-0

In [10]:
res2 = body_model(pose_rotvecs=fit_result['pose_rotvecs'], shape_betas=fit_result['shape_betas'])
res2['joints'] - res['joints']

/home/sarandi/rwth-home2/pose/pycharm/smplfit/smplfit/np/rotation.py:15: RuntimeWarning: invalid value encountered in divide
  axis = np.nan_to_num(rotvec / angle)


array([[[ 2.7845497e-05, -9.4366074e-04,  1.5405584e-03],
        [-1.1974592e-03, -1.6878247e-03,  2.1736231e-03],
        [-1.0950267e-03,  7.3134899e-04,  1.9258577e-03],
        [ 1.7719790e-03, -1.4712512e-03,  7.8488514e-04],
        [ 1.2356043e-04,  1.2022704e-02,  1.1742264e-03],
        [ 3.5900772e-03,  3.6231279e-03,  8.5595995e-04],
        [ 8.4513426e-04,  1.0751188e-03,  4.5847446e-03],
        [ 6.2587261e-03, -6.8422556e-03,  9.5307529e-03],
        [-4.7744215e-03,  7.5458884e-03,  1.2028180e-02],
        [ 3.3453107e-05,  1.0608286e-03,  1.7858073e-03],
        [ 8.8137388e-03, -9.3997121e-03,  1.2855828e-03],
        [ 2.6093274e-03,  2.0848274e-02,  4.1043386e-03],
        [ 7.0183277e-03, -3.1509995e-03,  8.2904175e-03],
        [ 4.6474934e-03, -2.0354092e-03,  5.3794459e-03],
        [ 5.2588880e-03, -3.6215782e-04,  5.2741691e-03],
        [-6.3502789e-04,  5.0564483e-03,  6.2255636e-03],
        [ 4.3415129e-03,  2.2546351e-03,  5.6001171e-03],
        [ 8.55

In [1]:
from smplfit.tf.fitting import Fitter
from smplfit.tf.smpl import SMPL
import numpy as np
import tensorflow as tf
import os
os.environ['DATA_ROOT'] = '/work/sarandi/data'
v_ = tf.convert_to_tensor(v, tf.float32)

body_model = SMPL(model_name='smpl', gender='neutral')
fitter = Fitter(body_model, num_betas=10)
fit_result = fitter.fit(v_, n_iter=3, beta_regularizer=1,
                        requested_keys=['pose_rotvecs', 'shape_betas'])
fit_result['pose_rotvecs'], fit_result['shape_betas'], fit_result['trans']

2024-10-29 03:52:41.756352: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-10-29 03:52:41.756378: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-10-29 03:52:41.757536: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-10-29 03:52:41.763007: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-10-29 03:52:42.340760: W tensorflow/compiler/tf2

ImportError: cannot import name 'Fitter' from 'smplfit.tf.fitting' (/home/sarandi/rwth-home2/pose/pycharm/smplfit/smplfit/tf/fitting.py)